In [1]:
from datetime import datetime

import dask.dataframe as dd
import dask_geopandas
import geopandas
import pandas as pd
from bokeh.models import (
    ColumnDataSource,
    HoverTool,
    Legend,
    Span,
    TabPanel,
    Tabs,
    Text,
    Title,
)
from bokeh.plotting import figure, output_notebook, show
from distributed import Client

# Estimating Activity based on Point of Interest Visitation

Estimating **visitation** within or in the proximity to points of interest, such as residential, commercial and industrial, zones can potentially provide insights in the aftermath of the [earthquakes near Nurdağı, Türkiye](https://www.usgs.gov/news/featured-story/m78-and-m75-kahramanmaras-earthquake-sequence-near-nurdagi-turkey-turkiye). Similarly to [Google Community Mobility Reports](https://www.google.com/covid19/mobility/) (now discontinued), the following working methodology seeks to capture the change in mobility (i.e., number of visits) within OpenStreetMap points of interest compared to a baseline (Jan-23). Note that the mobility data represents a subset of the total population in an area, specifically only users that turned on the Location Services device setting on their mobile device. This is not the total population density.

In [2]:
client = Client(n_workers=2)
client

<Client: 'tcp://127.0.0.1:64354' processes=2 threads=8, memory=16.00 GiB>

## Data

In this section, we import from the data sources manipulated throughout the notebook. Note that `data` is a placeholder location where we recommended to place the interim data. When using non-public data, please carefully  abide by the terms and conditions and data classification. 

In [3]:
COLORS = [
    "#4E79A7",  # Blue
    "#F28E2B",  # Orange
    "#E15759",  # Red
    "#76B7B2",  # Teal
    "#59A14F",  # Green
    "#EDC948",  # Yellow
    "#B07AA1",  # Purple
    "#FF9DA7",  # Pink
    "#9C755F",  # Brown
    "#BAB0AC",  # Gray
    "#7C7C7C",  # Dark gray
    "#6B4C9A",  # Violet
    "#D55E00",  # Orange-red
    "#CC61B0",  # Magenta
    "#0072B2",  # Bright blue
    "#329262",  # Peacock green
    "#9E5B5A",  # Brick red
    "#636363",  # Medium gray
    "#CD9C00",  # Gold
    "#5D69B1",  # Medium blue
]

In [4]:
# https://papermill.readthedocs.io/en/latest/usage-parameterize.html
COUNTRY = "TR"
PANEL = "v2023.3.19"
TAG = "landuse"

### Area of Interest

In this study, the **area of interest** is defined as the [affected 11 provinces in Türkiye](https://reliefweb.int/report/turkiye/turkey-earthquake-emergency-situation-report-17022023) and the area highlighted in northern Syria as shown below. 

In [5]:
AOI = geopandas.read_file("../../data/interim/tessellation/SYRTUR_tessellation.gpkg")

In [6]:
AOI.explore(color="orange", style_kwds={"stroke": True, "opacity": 0.25})

### OpenStreetMap 

Using the [Humanitarian OpenStreetMap](https://hotosm.org)'s [Export Tool](https://export.hotosm.org/en/v3/), the project team obtained a OSM dataset of points of interest within a clipping boundary defined by the [area of interest](#area-of-interest) between Türkiye and Syria.

In [7]:
POI = dask_geopandas.read_file(
    "../../data/external/export.hotosm.org/hotosm_worldbank_tur_points_of_interest_gpkg.zip!hotosm_worldbank_tur_points_of_interest.gpkg",
    npartitions=16,
)

In [8]:
# POI["geometry"] = POI["geometry"].to_crs("EPSG:3857").buffer(100).to_crs("EPSG:4326")

To illustrate, we visualize below the points of interest tagged with `landuse=industrial`.

In [9]:
POI[POI[TAG].isin(["industrial"])].compute().explore(color="red")

### Veraset Movement

Veraset Movement provides a panel of human mobility data, based on data collection of GPS-enabled devices location.

In [10]:
ddf = dd.read_parquet(
    f"../../data/final/panels/{PANEL}",
    filters=[("country", "=", COUNTRY)],
)

Calculating `date` from the date and time the points were collected.

In [11]:
ddf["date"] = dd.to_datetime(ddf["datetime"].dt.date)

## Methodology

Similarly to [Google Community Mobility Reports](https://www.google.com/covid19/mobility/) (now discontinued), the following working methodology seeks to capture the change in mobility (i.e., number of visits) within OpenStreetMap points of interest compared to a baseline (Jan-23). Note that the mobility data represents a subset of the total population in an area, specifically only users that turned on the Location Services device setting on their mobile device. This is not the total population density.

Using [Dask-GeoPandas](https://dask-geopandas.readthedocs.io/en/stable/), we calculate the number of devices seen within the points of interest and aggregate by the `landuse` classication (e.g, residential), H3 index and date.

In [12]:
gddf = dask_geopandas.from_dask_dataframe(
    ddf,
    geometry=dask_geopandas.points_from_xy(ddf, "longitude", "latitude"),
).set_crs("EPSG:4326")

We execute a spatial join (without H3) to aggregate the number of devices for each spatial and temporal bin. In this case, we use `H3 resolution 6` and a daily aggregation.

In [13]:
result = (
    gddf.sjoin(POI, predicate="within")
    .groupby([TAG, "hex_id", "date"])["uid"]
    .nunique()
    .to_frame(name="count")
    .reset_index()
    .compute()
)

Finally, the results joined into administrative divisions. 

In [14]:
# result.to_parquet(f"../../data/final/{COUNTRY}_visits_by_{TAG}_{PANEL}.parquet")
# result = pd.read_parquet(f"../../data/final/{COUNTRY}_visits_by_{TAG}_{PANEL}.parquet")

In [15]:
result = result.merge(
    AOI[["hex_id", "ADM0_PCODE", "ADM1_PCODE", "ADM2_PCODE"]], on="hex_id"
)

In [16]:
result = result[result["ADM0_PCODE"] == "TR"]

## Results

In this section, we visualize the daily number of devices detected within each of the following OSM `landuse` classification.

In [17]:
FEATURES = [
    "residential",
    "commercial",
    "industrial",
    "education",
    "farmland",
    "construction",
]

In [18]:
result.sort_values(["date"])

landuse           hex_id       date  count ADM0_PCODE ADM1_PCODE  \
0         cemetery  862da8837ffffff 2023-01-01      1         TR     TUR027   
7910   residential  862dac077ffffff 2023-01-01      2         TR     TUR080   
19140  residential  862da170fffffff 2023-01-01     64         TR     TUR031   
7815        forest  862dac00fffffff 2023-01-01      3         TR     TUR080   
7814   residential  862dac00fffffff 2023-01-01      1         TR     TUR080   
...            ...              ...        ...    ...        ...        ...   
9632   residential  862dae807ffffff 2023-03-20     39         TR     TUR031   
20447   industrial  862da1247ffffff 2023-03-20      1         TR     TUR031   
13296     cemetery  862c3056fffffff 2023-03-20     14         TR     TUR021   
1188   residential  862d127b7ffffff 2023-03-20      5         TR     TUR001   
23051  residential  862da8907ffffff 2023-03-20      1         TR     TUR027   

      ADM2_PCODE  
0      TUR027008  
7910   TUR080001  
19140  TUR031014  
7815   TUR080003  
7814   TUR080003  
...          ...  
9632   TUR031013  
20447  TUR031009  
13296  TUR021015  
1188   TUR001015  
23051  TUR027008  

[32242 rows x 7 columns]

In [19]:
def plot_visitation(data, title="POI Visitation"):
    """Plot number of visits to OSM points of interest"""

    p = figure(
        title=title,
        width=700,
        height=600,
        x_axis_label="Date",
        x_axis_type="datetime",
        y_axis_label="Number of devices",
        y_axis_type="log",
        y_range=(1, 10**5),
        tools="pan,wheel_zoom,box_zoom,reset,save,box_select",
    )
    p.add_layout(Legend(), "right")
    p.add_layout(
        Title(
            text=f"Number of devices detected within OSM '{TAG}' for each 3-day time window",
            text_font_size="12pt",
            text_font_style="italic",
        ),
        "above",
    )
    p.add_layout(
        Title(
            text=f"Source: Veraset Movement. Creation date: {datetime.today().strftime('%d %B %Y')}. Feedback: datalab@worldbank.org.",
            text_font_size="10pt",
            text_font_style="italic",
        ),
        "below",
    )
    
    # plot spans
    p.renderers.extend(
        [
            Span(
                location=datetime(2023, 2, 6),
                dimension="height",
                line_color="grey",
                line_width=2,
                line_dash=(4, 4),
            ),
            Span(
                location=datetime(2023, 2, 20),
                dimension="height",
                line_color="grey",
                line_width=2,
                line_dash=(4, 4),
            ),
        ]
    )
    
    # plot lines
    renderers = []
    for column, color in zip(FEATURES, COLORS):
        try:
            r = p.line(
                data.index[:-1],
                data[column][:-1],
                legend_label=column,
                line_color=color,
                line_width=2,
            )
            renderers.append(r)
        except:
            pass
        
    p.add_tools(
        HoverTool(
            tooltips="date: @x{%F}, devices: @y",
            formatters={"@x": "datetime"},
        )
    )

    p.legend.location = "bottom_left"
    p.legend.click_policy = "hide"
    p.title.text_font_size = "16pt"
    p.sizing_mode = "scale_both"
    return p

### By total area

By aggregating the visitation tally, we show a smoothed representation of how many users were detected within the total area for each 3-day time period. 

In [20]:
data = (
    result.pivot_table("count", index=["date"], columns=[TAG], aggfunc="sum")
    .groupby(pd.Grouper(freq="3D"))
    .sum()
)

In [21]:
output_notebook()
show(plot_visitation(data))

Loading BokehJS ...

### By first-level administrative divisions

By aggregating the visitation tally, we show a smoothed representation of how many users were detected within each first-level administrative division and for each 3-day time period. 

In [22]:
tabs = []

# iterate over first-level administrative divisions
for pcode in sorted(result["ADM1_PCODE"].unique()):
    data = (
        result[result["ADM1_PCODE"] == pcode]
        .pivot_table("count", index=["date"], columns=[TAG], aggfunc="sum")
        .groupby(pd.Grouper(freq="3D"))
        .sum()
    )
    tabs.append(
        TabPanel(
            child=plot_visitation(data, title=f"Points of Interest Visits in {pcode}"),
            title=pcode,
        )
    )

# plot panel
tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs)

## Limitations

```{warning}
 Note that the mobility data represents a subset of the total population in an area, specifically only users that turned on the Location Services device setting on their mobile device. This is not the total population density.
```